In [1]:
import pandas as pd
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", 400)
import Random_event_simulation as rand_event
import Visu_data as visu
import numpy as np
import plotly.graph_objects as go
import Hill_Estimator as he

# Data analysis

In [2]:
df = pd.read_csv("data.csv")
data = visu.data_analysis(df)
print("Data loaded and analysed")

Data loaded and analysed


In [ ]:
df_trade = df[df["action"] == "T"]
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_trade["ts_event"], y=df_trade["price"], mode='lines', name='Trade'))
fig.update_layout(title="Trade Events", xaxis_title="Timestamp", yaxis_title="Price")
fig.show()

In [3]:
data.stats_()

 -- Dataset statistics -- 

Tick                                  : 0.01
Average Bid-ask                       : 0.017883881281608775
Number of Jumps of more than just one : 2671
Number of Jumps of less than just one : 11544
Average jump size (up)                : 1.328181164629759
Average jump size (down)              : -1.2658523908523873
Number of up jumps                    : 11128
Number of down jumps                  : 11544

 -- Graphs -- 


In [4]:
data.data_hawkes()

# Hill Estimator

In [5]:
N, M = 1000, 50
datas = ["constant", "cauchy", "levy"]
for str_data in datas:
    print(f"Data type: {str_data}")
    he.plot_hill_estimation(*he.test_on_synthetic_data(N, M, str_data))

Data type: constant


Data type: cauchy


Data type: levy


In [6]:
jump_down = data.jump_counts_down
jump_up = data.jump_counts_up

X = []
for key, value in jump_down.items():
    X += [key] * value
for key, value in jump_up.items():
    X += [key] * value
X = np.array(X)

In [7]:
he.plot_hill_estimation_real_data(*he.test_on_real_data(X))

# Hawkes Fit Exponential Univariate

In [8]:
T_max     = 10000
nb_points = 20
M_max     =  1

lambda_0 = 0.1

alpha = 0.3
beta = 2
def kernel(t):
    return alpha*np.exp(-beta*t)

process = rand_event.Hawkes_process(T_max, lambda_0 = lambda_0, kernel = kernel, kernel_type = 'Exp', alpha_exp = alpha, beta_exp = beta)
print(len(process.simulate_by_thinning_exponential()))
process.exponential_estimation()

4694
Optimal lambda   = 0.3980532420512873
Optimal beta     = 2.0563858173117797
Optimal alpha    = 0.2908482743882003
Maximum log-like = 34601.679719973574


(np.float64(0.2908482743882003),
 np.float64(2.0563858173117797),
 np.float64(0.3980532420512873))

In [9]:
T_max     = 50
nb_points = 20
M_max     =  1

lambda_0 = 100
k = 0.01
c = 1
p = 1.3

def kernel(t):
    return k/(c+t)**p

print(lambda_0/(1 - k/(p-1)*c**p)*T_max)

process = rand_event.Hawkes_process(T_max, c_pl=c, p_pl = p, k_pl = k, lambda_0 = lambda_0, kernel = kernel)#, kernel_type = 'Power_Law')
# process.visu_intensity(nb_points, 'Power_Law')
process.power_law_estimation(reg_term = 0)

5172.413793103448


KeyboardInterrupt: 

In [ ]:
# Paramètres globaux
T_max = 100.0  # durée maximale de l'observation

# Création d'une instance avec noyau power law
hawkes = rand_event.Hawkes_process(T_max=T_max, lambda_0=1, kernel_type='Power_Law', c_pl=1.0, p_pl=1.5, k_pl=0.5)

# 1. Entraînement du réseau de neurones
window_length = 25      # taille de la fenêtre d'événements pour le réseau
N_simulations = 200000     # nombre de simulations pour l'entraînement
epochs = 50             # nombre d'époques d'entraînement
lr = 1e-3               # taux d'apprentissage

print("Entraînement du modèle DL...")
hawkes.fit_power_law_DL(length=window_length, N_simulations=N_simulations, epochs=epochs, lr=lr)

# 2. Simulation d'une nouvelle série d'événements avec des paramètres connus
# Choisissons des paramètres "vrais"
lambda_true = 30
k_true = 0.6
c_true = 1.0
p_true = 1.0

# Simulation d'une série de longueur 200 (par exemple)
new_events = hawkes.simulate_hawkes_power_law(length=3000, lambda_true=lambda_true,
                                                k_true=k_true, c_true=c_true, p_true=p_true)
print(f"Nouvelle série simulée avec {len(new_events)} événements.")

# 3. Estimation des paramètres sur la nouvelle série à l'aide du réseau de neurones
estimation = hawkes.predict_parameters(new_events)
print("\nParamètres estimés (moyenne sur fenêtres glissantes) :")
print(estimation)

print(f'lambda_true = {lambda_true}, k_true = {k_true}, c_true = {c_true}, p_true = {p_true}')

# Visualisation simple de la série d'événements
fig = go.Figure()
fig.add_trace(go.Scatter(x=new_events, y=np.arange(len(new_events)), mode='lines+markers',
                        name="Processus Hawkes simulé"))
fig.update_layout(title="Série d'événements simulée",
                xaxis_title="Temps",
                yaxis_title="Nombre d'événements")
fig.show()

KeyboardInterrupt: 

In [ ]:
file = '/Users/edouard/Desktop/EA p1  HFT/HFT_QR_RL_save/Sans titre/HFT_QR_RL/data/MBO-10 analyse_2/test_csv/xnas-itch-20240726.mbp-10.csv'
df   = pd.read_csv(file)
df.head()

In [ ]:
data = visu.data_analysis(df)
data.stats_()

In [ ]:
alpha_plus, beta_plus, lambda_plus, alpha_minus, beta_minus, lambda_minus = data.fit('Exp_univariate',visu = True)
print(alpha_plus, beta_plus, lambda_plus, alpha_minus, beta_minus, lambda_minus)

In [ ]:
_,_ = data.simulate_exp_univariate(18000, alpha_plus, beta_plus, lambda_plus, alpha_minus, beta_minus, lambda_minus, 165, tick = 0.01, visu = True, show_real_p = True)


# Hawkes Multivariate

In [ ]:
T_max = 500
lambda_1, lambda_2 = 1, 1
alpha_11, alpha_12, alpha_21, alpha_22 = 0.5, 0.1, 0.21, 0.5
beta_11, beta_12, beta_21, beta_22 = 0.7, 0.8, 0.6, 0.7
hawkes_bi = rand_event.Hawkes_process_bivariate(T_max, lambda_0_1=lambda_1, lambda_0_2=lambda_2, alpha_11=alpha_11, beta_11=beta_11, alpha_12=alpha_12, beta_12=beta_12,
                                     alpha_21=alpha_21, beta_21=beta_21, alpha_22=alpha_22, beta_22=beta_22)

In [ ]:
alpha = np.array([[alpha_11, alpha_12], [alpha_21, alpha_22]])
eiv = np.linalg.eigvals(alpha)
print(f"Le rayon spectral de alpha est {max(np.abs(eiv))}")

In [ ]:
P1, P2 = hawkes_bi.simulate_by_thinning_exponential()

t = np.linspace(0, T_max, 1000)
N1, N2 = [np.sum(np.array(P1) < t_i) for t_i in t], [np.sum(np.array(P2) < t_i) for t_i in t]

fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=N1, mode='lines', name='N1'))
fig.add_trace(go.Scatter(x=t, y=N2, mode='lines', name='N2'))
fig.show()

In [ ]:
estimated_params = hawkes_bi.exponential_estimation()
print("Real parameters:")
print(f"λ1 = {lambda_1}, λ2 = {lambda_2}")
print(f"α11 = {alpha_11}, α12 = {alpha_12}, α21 = {alpha_21}, α22 = {alpha_22}")
print(f"β11 = {beta_11}, β12 = {beta_12}, β21 = {beta_21}, β22 = {beta_22}")